In [2]:
import os
import json

from sentence_transformers import SentenceTransformer

model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')

c:\Users\Jose\Desktop\Nuanced_Recommendation_System\.venv\Lib\site-packages\sentence_transformers\cross_encoder\CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange
c:\Users\Jose\Desktop\Nuanced_Recommendation_System\.venv\Lib\site-packages\transformers\tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [3]:
def update_filters(filters, data):
    for key, value in filters.items():
        dont_add = ['Boys Love', 'Erotica', 'Girls Love', 'Hentai', 'Ecchi', 'Gore', 'Crossdressing', 'Magical Sex Shift', 'Rx - Hentai', 'R+ - Mild Nudity']
        if data[key] and key == 'rating':
            if data[key] not in dont_add:
                value.add(data[key])
        else:
            for val in data[key]:
                if val and val not in dont_add:
                    value.add(val)
    return filters

In [ ]:
def clean_filters(filters):
    for key, val in filters.items():
        val.add('ALL')
        filters[key] = list(val)
    return filters

In [ ]:
print('Embedding Started')

filters = {
'genres': set(),
'themes': set(),
'rating': set()
}

embeddings = {}
for name in os.listdir('./anime'):
    with open(f"./anime/{name}", 'r') as file:
        data = json.load(file)

    if not data:
        continue

    filters = update_filters(filters, data)

    name = name.replace('.json', '')
    
    data['image'] = f"./images/{name}.jpg"

    text = f'''Episodes: {data['episodes']} 
            Premiered: {data['premiered']} 
            Broadcast: {data['broadcast']} 
            Producers: {' '.join(data['producers'])} 
            Licensors: {' '.join(data['licensors'])} 
            Studios: {' '.join(data['studios'])} 
            Source: {' '.join(data['source'])}  
            Genres: {' '.join(data['genres'])} 
            Themes: {' '.join(data['themes'])} 
            Demographic: {data['demographic']} 
            Duration: {data['duration']} 
            Rating: {data['rating']} 
            Description: {data['description']}'''
    
    embeddings[name] = data.copy()
    
    embeddings[name]['objective_embedding'] = [model.encode(text).tolist()]
    subjective_embeddings = []
    for review in embeddings[name]['reviews']:
        text = review['text']
        subjective_embeddings.append(model.encode(text).tolist())
        data['review'] = text
    embeddings[name]['subjective_embeddings'] = subjective_embeddings

filters = clean_filters(filters)

with open('./embeddings/data.json', 'w') as f:
    json.dump({'embeddings':embeddings, 'filters': filters}, f)

print('Embedding Complete')